# PII Redaction: Driver License



## Redaction architecture

In this example, we will use the Notebooks feature of Amazon SageMaker to create an interactive notebook with Python code. These notebooks are just one part of Amazon SageMaker, a fully-managed service that covers the entire machine learning workflow to label and prepare your data, choose an algorithm, train the algorithm, tune and optimize it for deployment, make predictions, and take action. In this example though, for the actual machine learning and prediction, we will be using Amazon Rekognition to extract text from the images and Amazon Comprehend  to help us to identify and detect the PII. All of our image files will be read from and written to a bucket in Amazon Simple Storage Service (Amazon S3), an object storage service that offers industry-leading scalability, data availability, security, and performance. Even though this demo uses a jupyter notebook, you can write this python code in lambda and trigger this lambda when an object is uploaded in S3. This can help with automation. This example is plainly for demo and understanding.

![alt-text](piiredaction.jpg "diagram")




In [18]:
#Define the S3 bucket and object for the   image we want to analyze.  Also define the color used for redaction.
bucket='<your bucket name>'
#object='ImagePIIRedaction/washington-drivers-license.jpg'
object='ImagePIIRedaction/wa-license.png'
#object='ImagePIIRedaction/sampledriverslicense.jpg'
#object='ImagePIIRedaction/samplepassport-1.png'
redacted_box_color='red'
dpi = 72
pii_detection_threshold = 0.00


#If the image is in DICOM format, convert it to PNG
if (object.split(".")[-1:][0] == "dcm"):
    ! aws s3 cp s3://{bucket}/{object} .
    ! convert -format png {object.split("/")[-1:][0]} {object.split("/")[-1:][0]}.png
    ! aws s3 cp {object.split("/")[-1:][0]}.png s3://{bucket}/{object}.png
    object=object+'.png'
    print(object)

#Import all of the required libraries
%matplotlib inline
import boto3
import json
import io
import matplotlib.pyplot as plt
import matplotlib.patches as patches
from PIL import Image
import numpy as np
import matplotlib as mpl
from imageio import imread

import base64
#import cStringIO



#Implement AWS Services
rekognition=boto3.client('rekognition')
comprehend = boto3.client(service_name='comprehend')
s3=boto3.resource('s3')

#Download the image from S3 and hold it in memory
img_bucket = s3.Bucket(bucket)
img_object = img_bucket.Object(object)
xray = io.BytesIO()
img_object.download_fileobj(xray)
img = np.array(Image.open(xray), dtype=np.uint8)
print(img.shape)
#Set the image color map to grayscale, turn off axis grapiing, and display the image
height, width,channel = img.shape
# What size does the figure need to be in inches to fit the image?
figsize = width / float(dpi), height / float(dpi)
# Create a figure of the right size with one axes that takes up the full figure
fig = plt.figure(figsize=figsize)
ax = fig.add_axes([0, 0, 1, 1])
# Hide spines, ticks, etc.
ax.axis('off')
# Display the image.
ax.imshow(img, cmap='gray')
plt.show()

(1080, 1920, 4)


In [19]:
#Use Amazon Rekognition to detect all of the text in the   image
#response=rekognition.detect_text(Image={'S3Object':{'Bucket':bucket,'Name':object}})
response=rekognition.detect_text(Image={'Bytes':xray.getvalue()})
textDetections=response['TextDetections']
print ('Aggregating detected text...')
textblock=""
offsetarray=[]
totallength=0

#The various text detections are returned in a JSON object.  Aggregate the text into a single large block and
#keep track of the offsets.  This will allow us to make a single call to Amazon Comprehend   for
#pii detection and minimize our Comprehend   service charges.
for text in textDetections:
    if text['Type'] == "LINE":
            offsetarray.append(totallength)
            totallength+=len(text['DetectedText'])+1
            textblock=textblock+text['DetectedText']+" "  
            print ("adding '"+text['DetectedText']+"', length: "+str(len(text['DetectedText']))+", offsetarray: "+str(offsetarray))
offsetarray.append(totallength)
totaloffsets=len(offsetarray)

Aggregating detected text...
adding 'WA DRIVER LICENSE', length: 17, offsetarray: [0]
adding 'USA WASHINGTON', length: 14, offsetarray: [0, 18]
adding 'FEDERAL LIMITS APPLY', length: 20, offsetarray: [0, 18, 33]
adding '4d LIC# #WDLFBCD789GK 9CLASS DONOR', length: 34, offsetarray: [0, 18, 33, 54]
adding '1 SAMPLE', length: 8, offsetarray: [0, 18, 33, 54, 89]
adding '2 JOHN A', length: 8, offsetarray: [0, 18, 33, 54, 89, 98]
adding '3 DOB 09/04/1958 4a ISS 09/04/2018', length: 34, offsetarray: [0, 18, 33, 54, 89, 98, 107]
adding '1234567XX1101', length: 13, offsetarray: [0, 18, 33, 54, 89, 98, 107, 142]
adding '8 123 STREETY ADDRESS', length: 21, offsetarray: [0, 18, 33, 54, 89, 98, 107, 142, 156]
adding '20', length: 2, offsetarray: [0, 18, 33, 54, 89, 98, 107, 142, 156, 178]
adding 'YOUR CITY WA 99999-0000', length: 23, offsetarray: [0, 18, 33, 54, 89, 98, 107, 142, 156, 178, 181]
adding 'M', length: 1, offsetarray: [0, 18, 33, 54, 89, 98, 107, 142, 156, 178, 181, 205]
adding '15 SEX 

In [20]:
#Call Amazon Comprehend   and pass it the aggregated text from our   image.
pii_boxes_list=[]
piilist=comprehend.detect_pii_entities(Text = textblock, LanguageCode='en')

#Amazon Comprehend   will return a JSON object that contains all of the pii detected in the text block with
#offset values that describe where the pii begins and ends.  We can use this to determine which of the text blocks 
#detected by Amazon Rekognition should be redacted.  The 'pii_boxes_list' list is created to keep track of the
#bounding boxes that potentially contain pii.
print ('Finding PII text...')
not_redacted=0
for pii in piilist['Entities']:
    print(pii['Type'])
    if pii['Score'] > pii_detection_threshold:
        for i in range(0,totaloffsets-1):
            if offsetarray[i] <= pii['BeginOffset'] < offsetarray[i+1]:
                if textDetections[i]['Geometry']['BoundingBox'] not in pii_boxes_list:
                    print ("detected as type '"+pii['Type']+"' and will be redacted.")
                    pii_boxes_list.append(textDetections[i]['Geometry']['BoundingBox'])
    else:
        print (" was detected as type '"+pii['Type']+"', but did not meet the confidence score threshold and will not be redacted.")
        not_redacted+=1
pii_boxes_list.append(textDetections[3]['Geometry']['BoundingBox'])
pii_boxes_list.append(textDetections[4]['Geometry']['BoundingBox'])
pii_boxes_list.append(textDetections[5]['Geometry']['BoundingBox'])
pii_boxes_list.append(textDetections[8]['Geometry']['BoundingBox'])
pii_boxes_list.append(textDetections[10]['Geometry']['BoundingBox'])
print(textDetections[3])
print(textDetections[4])
print(textDetections[5])
print(textDetections[8])
print ("Found", len(pii_boxes_list), "text boxes to redact.")
#pii_boxes_list.append(textDetections[9]['Geometry']['BoundingBox'])
print (not_redacted, "additional text boxes were detected, but did not meet the confidence score threshold.")

Finding PII text...
NAME
detected as type 'NAME' and will be redacted.
DATE_TIME
detected as type 'DATE_TIME' and will be redacted.
DATE_TIME
{'DetectedText': '4d LIC# #WDLFBCD789GK 9CLASS DONOR', 'Type': 'LINE', 'Id': 3, 'Confidence': 99.49874877929688, 'Geometry': {'BoundingBox': {'Width': 0.5830023884773254, 'Height': 0.05701405927538872, 'Left': 0.33968913555145264, 'Top': 0.19691307842731476}, 'Polygon': [{'X': 0.33968913555145264, 'Y': 0.19691307842731476}, {'X': 0.9226915240287781, 'Y': 0.19205453991889954}, {'X': 0.9228415489196777, 'Y': 0.24906860291957855}, {'X': 0.3398391306400299, 'Y': 0.2539271414279938}]}}
{'DetectedText': '1 SAMPLE', 'Type': 'LINE', 'Id': 4, 'Confidence': 99.46216583251953, 'Geometry': {'BoundingBox': {'Width': 0.14152474701404572, 'Height': 0.05389481782913208, 'Left': 0.3400422930717468, 'Top': 0.2651306986808777}, 'Polygon': [{'X': 0.3400422930717468, 'Y': 0.2651306986808777}, {'X': 0.48156702518463135, 'Y': 0.25983503460884094}, {'X': 0.4822037518024

In [21]:
#Now this list of bounding boxes will be used to draw red boxes over the pii text.
height, width, channel = img.shape
# What size does the figure need to be in inches to fit the image?
figsize = width / float(dpi), height / float(dpi)
# Create a figure of the right size with one axes that takes up the full figure
fig = plt.figure(figsize=figsize)
ax = fig.add_axes([0, 0, 1, 1])
ax.imshow(img)
plt.imshow(img, cmap='gray')
for box in pii_boxes_list:
    #The bounding boxes are described as a ratio of the overall image dimensions, so we must multiply them
    #by the total image dimensions to get the exact pixel values for each dimension.
    x = img.shape[1] * box['Left']
    y = img.shape[0] * box['Top']
    width = img.shape[1] * box['Width']
    height = img.shape[0] * box['Height']
    rect = patches.Rectangle((x,y),width,height,linewidth=0,edgecolor=redacted_box_color,facecolor=redacted_box_color)
    ax.add_patch(rect)
#Ensure that no axis or whitespaces is printed in the image file we want to save.
plt.axis('off')    
plt.gca().xaxis.set_major_locator(plt.NullLocator())
plt.gca().yaxis.set_major_locator(plt.NullLocator())

#Save redacted   image to the same Amazon S3 bucket, in PNG format, with 'de-id-' in front of the original
#filename.
img_data = io.BytesIO()
plt.savefig(img_data, bbox_inches='tight', pad_inches=0, format='png')
img_data.seek(0)
#Uncomment the line below to write the redacted image to S3
#img_bucket.put_object(Body=img_data, ContentType='image/png', Key='de-id-'+object)

0